In [1]:
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
import matplotlib.pyplot as plt
from IPython import display
from tensorflow.python.client import device_lib
import os
import re

In [2]:
print(device_lib.list_local_devices())
gpus = tf.config.list_physical_devices('GPU')
os.environ["TF_FORCE_GPU_ALLOW_GROWTH"]="true"
if gpus:
  # Restrict TensorFlow to only use the first GPU
  try:
    tf.config.experimental.set_visible_devices(gpus[0], 'GPU')
    logical_gpus = tf.config.experimental.list_logical_devices('GPU')
    print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPU")
  except RuntimeError as e:
    # Visible devices must be set before GPUs have been initialized
    print(e)

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 3581072741492455363
xla_global_id: -1
]


In [3]:
def return_DataPathList(path="anno.csv"):
    f = open(path, mode="r", encoding="UTF-8")
    tmp = f.readlines()
    datalist = []
    for dpath in tmp:
        datalist.append(dpath.split(",")[0])
    f.close()
    return datalist

In [4]:
def return_Datalabel(path="anno.csv"):
    f = open(path, mode="r", encoding="UTF-8")
    tmp = f.readlines()
    datalist = []
    
    for dpath in tmp:
        tmp2 = dpath.split(",")[1].replace("\n", "")
        datalist.append([int(i) for i in tmp2])
    return datalist

In [5]:
return_Datalabel()

[[0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [0],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1],
 [1]

In [21]:
# 学習データのパス
datalist_train = return_DataPathList(path="anno_train.csv")
# 学習データのラベル
train_label = return_Datalabel(path="anno_train.csv")
# テストデータのパス
datalist_test = return_DataPathList(path="anno_test.csv")
# テストデータのラベル
test_label = return_Datalabel(path="anno_test.csv")

train_data = [] # 学習データを格納する
test_data = [] #　テストデータを格納する
tmp_data = 0 # 一時的に座標データを格納する
max = 0
for i in range(len(datalist_train)):
    tmp_data = pd.read_csv(datalist_train[i], header=None).values

    train_data.append(tmp_data)
for i in range(len(datalist_test)):
    tmp_data = pd.read_csv(datalist_test[i], header=None).values

    test_data.append(tmp_data)

In [22]:
train_data = np.array(train_data).astype(np.float32)
test_data = np.array(test_data).astype(np.float32)
train_label = np.array(train_label).astype(np.int64)
test_label = np.array(test_label).astype(np.int64)
train_data = np.expand_dims(train_data, -1)
test_data = np.expand_dims(test_data, -1)
test_label = keras.utils.to_categorical(test_label, 2)
train_label = keras.utils.to_categorical(train_label, 2)

In [23]:
dim1 = np.array([[1]]*len(train_data)).astype(np.int64)
dim2 = np.array([[1]]*len(test_data)).astype(np.int64)
#print(dim)
print(len(train_data[0]), len(train_data[0][0]), len(train_data), len(train_label))

15 14 38440 38440


In [24]:
train_dataset = tf.data.Dataset.from_tensor_slices((train_data, train_label))
test_dataset = tf.data.Dataset.from_tensor_slices((test_data, test_label))

In [25]:
# データのシャッフル
BATCH_SIZE = 10
SHUFFLE_BUFFER_SIZE = 1000000
train_dataset = train_dataset.shuffle(SHUFFLE_BUFFER_SIZE).batch(BATCH_SIZE)
test_dataset = test_dataset.batch(BATCH_SIZE)
print(train_dataset)

<BatchDataset element_spec=(TensorSpec(shape=(None, 15, 14, 1), dtype=tf.float32, name=None), TensorSpec(shape=(None, 2), dtype=tf.float32, name=None))>


In [26]:
def build_model(input_dim, output_dim, rnn_layers=5, rnn_units=128):
    """Model similar to DeepSpeech2."""
    # Model's input
    input_model = layers.Input((input_dim[0], input_dim[1]), name="input")
    # Expand the dimension to use 2D CNN.
    x = layers.Reshape((-1, input_dim[0], 1), name="expand_dim")(input_model)
    x = layers.Conv2D(32, kernel_size=(3, 3), activation="relu")(x)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Conv2D(64, kernel_size=(3, 3), activation="relu")(x)
    x = layers.MaxPooling2D(pool_size=(2, 2))(x)
    x = layers.Flatten()(x)
    x = layers.Dropout(0.5)(x)
    # Classification layer
    output = layers.Dense(units=output_dim, activation="softmax")(x)
    # Model
    model = keras.Model(input_model, output, name="Shogi-winner-model")
    # Optimizer
    opt = keras.optimizers.Adam(learning_rate=1e-6)
    # Compile the model and return
    model.compile(optimizer=opt, loss='categorical_crossentropy', metrics=["accuracy"])
    return model


model = build_model(
    input_dim=[15,14],
    output_dim=2,
    rnn_units=512
)
model.summary(line_length=110)

Model: "Shogi-winner-model"
______________________________________________________________________________________________________________
 Layer (type)                                    Output Shape                                Param #          
 input (InputLayer)                              [(None, 15, 14)]                            0                
                                                                                                              
 expand_dim (Reshape)                            (None, 14, 15, 1)                           0                
                                                                                                              
 conv2d (Conv2D)                                 (None, 12, 13, 32)                          320              
                                                                                                              
 max_pooling2d (MaxPooling2D)                    (None, 6, 6, 32)                   

In [28]:
%load_ext tensorboard
!rd /s /q logs

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [29]:
import datetime
log_dir = "logs/fit/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir, histogram_freq=1)
tensorboard_callback = []

In [ ]:
test_dataset = tf.data.Dataset.from_tensor_slices((test_data, test_label))
#test_dataset = test_dataset.batch()

model.fit(train_dataset, epochs=1200, batch_size=32)

Epoch 1/1200
3844/3844 [==============================] - 9s 2ms/step - loss: 1.5779 - accuracy: 0.5137
Epoch 2/1200
3844/3844 [==============================] - 8s 2ms/step - loss: 1.4132 - accuracy: 0.5116
Epoch 3/1200
3844/3844 [==============================] - 8s 2ms/step - loss: 1.3035 - accuracy: 0.5085
Epoch 4/1200
3844/3844 [==============================] - 9s 2ms/step - loss: 1.2002 - accuracy: 0.5095
Epoch 5/1200
3844/3844 [==============================] - 9s 2ms/step - loss: 1.1029 - accuracy: 0.5117
Epoch 6/1200
3844/3844 [==============================] - 8s 2ms/step - loss: 1.0289 - accuracy: 0.5142
Epoch 7/1200
3844/3844 [==============================] - 10s 3ms/step - loss: 0.9683 - accuracy: 0.5139
Epoch 8/1200
3844/3844 [==============================] - 11s 3ms/step - loss: 0.9155 - accuracy: 0.5155
Epoch 9/1200
3844/3844 [==============================] - 10s 3ms/step - loss: 0.8668 - accuracy: 0.5181
Epoch 10/1200
3844/3844 [==============================] - 9s

In [117]:
predictions = []
mydata = []
targets = []
piyo = []
tmpl = []
test_dataset = tf.data.Dataset.from_tensor_slices((test_data, test_label))
test_dataset = test_dataset.batch(1)
count = 0
for batch in test_dataset:
    X, y = batch
    batch_predictions = model.predict(X)
    predictions.extend(batch_predictions)

    for label in y:
        targets.append(label)

    mydata.append("1" if X[0].numpy()[12][2] else "0")
    tmpl.append(X[0][12][2])
    piyo.append(X)
    if count == 250:
        break
    for i in range(len(predictions)):
        print(f"Target       : {targets[i]}")
        print(f"machineScore : {mydata[i]}")
        print(f"Prediction   : {predictions[i]}")
        
        print("-" * 100)
    
    count = count+1

1/1 [==============================] - 0s 15ms/step
Target       : [1. 0.]
machineScore : 1
Prediction   : [0.5885785  0.41142145]
----------------------------------------------------------------------------------------------------
1/1 [==============================] - 0s 20ms/step
Target       : [1. 0.]
machineScore : 1
Prediction   : [0.5885785  0.41142145]
----------------------------------------------------------------------------------------------------
Target       : [1. 0.]
machineScore : 1
Prediction   : [0.85099137 0.14900866]
----------------------------------------------------------------------------------------------------
1/1 [==============================] - 0s 16ms/step
Target       : [1. 0.]
machineScore : 1
Prediction   : [0.5885785  0.41142145]
----------------------------------------------------------------------------------------------------
Target       : [1. 0.]
machineScore : 1
Prediction   : [0.85099137 0.14900866]
---------------------------------------------

In [310]:
koma_dic = {"K":1, "R":2, "B":3, "G":4, "S":5, "N": 6, "L": 7, "P": 8,
           "k": -1, "r": -2, "b":-3, "g":-4, "s": -5, "n": -6, "l": -7, "p": -8}
mochi_id = {"R":0, "B": 1, "G": 2, "S":3, "N": 4, "L": 5, "P": 6,
           "r":7, "b": 8, "g":9, "s":10, "n":11, "l":12, "p":13}
nari_dic = {"R":9, "B":10, "r": -9, "b":-10,
            "S":4, "N":4, "L":4, "P":4,
            "s":-4, "n":-4, "l":-4, "p":-4}
nari_dic_inv = {9:"竜", 10:"馬", -9:"v竜", -10:"v馬"}

In [216]:
koma_dic_inv = {v:k for k, v in koma_dic.items()}
mochi_id_inv = {v:k for k, v in mochi_id.items()}
decode_koma = {"K":" 玉", "R":" 飛", "B":" 角", "G":" 金", "S":" 銀", "N": " 桂", "L": " 香", "P": " 歩",
           "k": "v王", "r": "v飛", "b":"v角", "g":"v金", "s": "v銀", "n": "v桂", "l": "v香", "p": "v歩"}
number_dic = {1:"一", 2:"二", 3:"三", 4:"四", 5:"五", 6:"六", 7:"七", 8:"八", 9:"九", 10:"十"}

In [315]:
def shogi_table(vec):
    print("後手の持駒：", end="")
    for i in range(7,14):
        #print(vec.numpy()[10][i][0])
        if vec.numpy()[10][i][0]==1:
            print(f"{decode_koma[mochi_id_inv[i]][1]}", end=" ")
        elif int(vec.numpy()[10][i][0])!=0:
            print(f"{decode_koma[mochi_id_inv[i]][1]}{number_dic[int(vec.numpy()[10][i][0])]}", end=" ")
    print("\n  ９ ８ ７ ６ ５ ４ ３ ２ １")
    print("+---------------------------+")
    for j in range(9):
        print("|", end="")
        try:
            for k in vec.numpy()[j][:9]:
                if 0< abs(k.item()) < 9:
                    koma = koma_dic_inv[k.item()]
                    print(decode_koma[koma], end="")
                elif abs(k.item()) > 8:
                    print(nari_dic_inv[k.item()], end="")
                else:
                    print(" ・", end="")
            #print("/", end="")
            print(f"|{number_dic[j+1]}")
        except:
            print(f"|{number_dic[j+1]}")
    print("+---------------------------+")
    print("先手の持駒：", end="")
    for i in range(6):
        #print(vec.numpy()[9][i][0])
        if vec.numpy()[10][i][0]==1:
            print(f"{decode_koma[mochi_id_inv[i]]}", end=" ")
        elif vec.numpy()[10][i][0] != 0:
            print(f"{decode_koma[mochi_id_inv[i]]}{number_dic[int(vec.numpy()[10][i][0])]}", end=" ")
    print()

In [302]:
for i in piyo[101].numpy()[0]:
    for j in i:
        print(j, end="")
    print()

[-7.][-6.][-5.][-4.][-1.][0.][-5.][-6.][-7.][0.][0.][0.][0.][0.]
[0.][-2.][0.][0.][0.][0.][-4.][-3.][0.][0.][0.][0.][0.][0.]
[-8.][0.][-8.][-8.][-8.][-8.][0.][0.][-8.][0.][0.][0.][0.][0.]
[0.][0.][0.][0.][0.][0.][-8.][2.][0.][0.][0.][0.][0.][0.]
[0.][-8.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.]
[0.][0.][8.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.]
[8.][8.][0.][8.][8.][8.][8.][0.][8.][0.][0.][0.][0.][0.]
[0.][3.][4.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.]
[7.][6.][5.][0.][1.][4.][5.][6.][7.][0.][0.][0.][0.][0.]
[1.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.]
[0.][0.][0.][0.][0.][0.][1.][0.][0.][0.][0.][0.][0.][1.]
[12.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.]
[0.0202][0.98333335][0.9916667][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.][0.]


In [323]:
for i in range(len(predictions)):
    #print(piyo[i][0][0])
    #if i == 100:
        #print("!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!\n"*50)
    shogi_table(piyo[i][0])
    print(f"評価値       :{piyo[i].numpy()[0][12][2][0]}")
    print(f"評価値       :{piyo[i].numpy()[0][12][2][0]*5000}")
    print(f"Target       : {targets[i]}")
    print(f"machineScore : {mydata[i]}")
    print(f"Prediction   : {predictions[i]}")
    print("-" * 100)
#for i in piyo:
    #print(piyo[i].numpy()[0][12][2]*5000)

後手の持駒：
  ９ ８ ７ ６ ５ ４ ３ ２ １
+---------------------------+
|v香v桂v銀v金v王v金v銀v桂v香|一
| ・v飛 ・ ・ ・ ・ ・v角 ・|二
|v歩v歩v歩v歩v歩v歩v歩v歩v歩|三
| ・ ・ ・ ・ ・ ・ ・ ・ ・|四
| ・ ・ ・ ・ ・ ・ ・ ・ ・|五
| ・ ・ ・ ・ ・ ・ ・ 歩 ・|六
| 歩 歩 歩 歩 歩 歩 歩 ・ 歩|七
| ・ 角 ・ ・ ・ ・ ・ 飛 ・|八
| 香 桂 銀 金 玉 金 銀 桂 香|九
+---------------------------+
先手の持駒：
評価値       :0.018799999728798866
評価値       :93.99999864399433
Target       : [1. 0.]
machineScore : 1
Prediction   : [0.5885785  0.41142145]
----------------------------------------------------------------------------------------------------
後手の持駒：角 
  ９ ８ ７ ６ ５ ４ ３ ２ １
+---------------------------+
|v香v桂 ・v金v王v金 ・v桂v香|一
| ・v飛 ・ ・ ・ ・ ・ ・ ・|二
|v歩 ・v歩 ・v歩 ・v銀v歩v歩|三
| ・v歩 ・v歩v銀v歩v歩 ・ ・|四
| ・ ・ ・ ・ ・ ・ ・ 歩 ・|五
| ・ ・ 歩 ・ 歩 ・ 歩 ・ ・|六
| 歩 歩 ・ 歩 ・ 歩 銀 ・ 歩|七
| ・ 銀 玉 金 ・ ・ ・ 飛 ・|八
| 香 桂 ・ ・ ・ 金 ・ 桂 香|九
+---------------------------+
先手の持駒： 角 
評価値       :0.010400000028312206
評価値       :52.00000014156103
Target       : [1. 0.]
machineScore : 1
Prediction   : [0.85099137 0.14900866]
------------------------------

In [145]:
data_num = len(targets)
origin_acc = 0
model_acc = 0
for i in range(len(targets)):
    tmp = 1 if predictions[i][0] >= 0.5 else 0
    if int(mydata[i]) == targets[i][0]:
        origin_acc = origin_acc+1
    if tmp == targets[i][0]:
        model_acc = model_acc + 1
print(f"評価値のみの勝敗予測            :  {origin_acc/data_num * 100}%")
print(f"対局条件を加えたモデルの勝敗予測 :  {model_acc/data_num * 100}%")

評価値のみの勝敗予測            :  66.13545816733067%
対局条件を加えたモデルの勝敗予測 :  86.45418326693228%


In [ ]:
test_loss = model.evaluate(test_dataset)

In [119]:
len(piyo)

251

In [21]:
model_dir = "shogi-predict-model/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")

model.save(model_dir+".h5")